# Can I walk to the train?
In this notebook we'll be exploring the walkability of Klang Valley's train stations using isochrone maps
We will use Open Route Service's API to draw this and compile the results into a csv
The data gathered will be visualized to be understood
KL has multiple different train lines with varying levels of service spreading across a large area. There is a relatively large number of stations relative to the population however the accesibility of the stations seems to be an issue for pedestrians. We'll analyze each train station from different lines. And compile them later on to get an average to be compared with other cities

The work from this notebook was presented in a Twitter thread at the following link:- <br>
https://twitter.com/NabilErsyad/status/1325415849809727489?s=20

In [1]:
#folium is the library used to visualize maps
import folium
#library to call Open Route Service(ORS)'s client and requests
from openrouteservice import client
import pandas as pd 
import numpy as np 
import plotly as py

from datetime import date
from isochrones import * 

#i like to be able to see all my columns in a pandas dataframe. this would allow it 
pd.set_option("display.max_columns", None)


# Train Station isochrones

Let's visualize all the stations and the 15 minute walking radius on a map.
15 minutes is somewhat arbitrary but given malaysia's hot weather it seems the most fair amount of time that malaysian's can generally tolerate to walk outdoors

In [11]:
#Personal api_key stored in a config.py file that is in gitignore. Uncomment the following and provide your own ORS api for your own use
## api_key = "you api key " #Provide your personal API key

from config import api_key

clnt = client.Client(key=api_key) 


In [12]:
#loading up train station data. This file contains the csv data for KL train stations. 
file_url = 'resources/data/raw_data/klang_valley_stations.csv'

#Stop ID is unique for every station. So that column will be used for index
data = pd.read_csv(file_url, index_col="Stop ID")
print(data.head())
print(data.columns)

                  Name  Service Provider Name  Latitude   Longitude ROUTE ID  \
Stop ID                                                                        
KC04       TAMAN WAHYU  Keretapi Tanah Melayu  3.214544  101.672182       KC   
KC03      KAMPUNG BATU  Keretapi Tanah Melayu  3.204796  101.675646       KC   
KB01        MID VALLEY  Keretapi Tanah Melayu  3.118528  101.678985       KB   
KC02     BATU KENTOMEN  Keretapi Tanah Melayu  3.198336  101.681163       KC   
KC05        BATU CAVES  Keretapi Tanah Melayu  3.237887  101.681187       KC   

            Route Name Line Number Line Colour Colour Hex Code          City  
Stop ID                                                                       
KC04     Seremban Line           1        Blue         #0000FF  Kuala Lumpur  
KC03     Seremban Line           1        Blue         #0000FF  Kuala Lumpur  
KB01     Seremban Line           1        Blue         #0000FF  Kuala Lumpur  
KC02     Seremban Line           1        Bl

# isochrone.py package and ORS client to get isochrones
We'll be using the function toMap() that was imported from the custom isochrone.py package. 
All you need for the function are:<br>
-- dataframe with the columns - ['Name','Route Name','Latitude','Longitude'] that would be sufficient to draw isochrone maps for train stations.<br>
-- param_iso - dictionary with the parameters of the isochrone <br>
-- client - the open route service api client <br>

Will return isochrone map of a transit line and dictionary of stations

In [16]:
#the way I coded this is that I want maps that will display train stations by lines. So that it wouldnt clutter the map.
lines = list(data['Route Name'].unique())
maps = []
params_iso = {'profile': 'foot-walking', 
              'range': [900], # 900/60 = 15 mins
              'interval': 300,
              'attributes': ['area', 'reachfactor', 'total_pop'] # Get population count for isochrones
             }
#By creating a list of train lines, i can iterate through each of them and create map objects for each train line.  
# 
# I should edit the toMap function, if params_iso or client is not passed then just map without calling isochrones from ORS           
for line in lines:
    maps.append(toMapORS(data,line,params_iso,clnt))

Retrieving Isochrone of TAMAN WAHYU station
Success
Retrieving Isochrone of KAMPUNG BATU station
Success
Retrieving Isochrone of MID VALLEY station
Success
Retrieving Isochrone of BATU KENTOMEN station
Success
Retrieving Isochrone of BATU CAVES station
Success
Retrieving Isochrone of SEPUTEH station
Success
Retrieving Isochrone of SENTUL station
Success
Retrieving Isochrone of PUTRA station
Success
Retrieving Isochrone of BANK NEGARA station
Success
Retrieving Isochrone of KUALA LUMPUR station
Success
Retrieving Isochrone of SALAK SELATAN station
Success
Retrieving Isochrone of BANDAR TASIK SELATAN station
Success
Retrieving Isochrone of SERDANG station
Success
Retrieving Isochrone of BANGI station
Success
Retrieving Isochrone of UKM station
Success
Retrieving Isochrone of KAJANG station
Success
Retrieving Isochrone of NILAI station
Success
Retrieving Isochrone of LABU station
Success
Retrieving Isochrone of BATANG BENAR station
Success
Retrieving Isochrone of TIROI station
Success
Ret

Timeout: 

# Saving isochrone data into CSVs
Once all the Isochrone requests are completed, I would want to store the data first into CSVs for future references. <br>
The following helper functions from isochrones.py will do that<br>
dictToDataFrame(maps,dataframe)
areaToDataframe(data)

In [5]:
#saves the data with the isochrones  data into new csv files
data = dictToDataFrame(maps,data)
file_url ='resources/data/klang_valley_stations_isochrones_' + str(date.today())+ '.csv'
data.to_csv(file_url)

In [6]:
#used to extract more specific data from isochrone data.
data = pd.read_csv(file_url)
data  = areaToDataframe(data)
data.to_csv(file_url)


In [7]:
maps[0][1].keys()

dict_keys(['KC04', 'KC03', 'KB01', 'KC02', 'KC05', 'KB02', 'KC01', 'KA04', 'KA03', 'KA02', 'KB03', 'KB04', 'KB05', 'KB08', 'KB07', 'KB06', 'KB10', 'KB11', 'KB09', 'KB12', 'KB13', 'KB14', 'KB15', 'KB16', 'KB17', 'KA01'])

In [8]:
maps[0][0]

In [9]:
maps[1][0]

In [10]:
maps[2][0]

In [11]:
maps[3][0]

In [12]:
maps[4][0]

In [13]:
maps[5][0]

In [14]:
maps[6][0]

In [15]:
maps[7][0]

In [16]:
maps[8][0]

In [17]:
maps[9][0]

In [18]:
maps[10][0]

# Singapore
Will be doing the same but with Singapore train station data

In [156]:
#loading up train station data.
file_url = '../resources/data/mrtsg.csv'

data_sg = pd.read_csv(file_url, index_col="OBJECTID")
lines = list(data_sg['Route Name'].unique())
map_sg = []
params_iso = {'profile': 'foot-walking', 
              'range': [900], # 900/60 = 15 mins
              'interval': 300,
              'attributes': ['area', 'reachfactor', 'total_pop'] # Get population count for isochrones
             }
for line in lines:
    map_sg.append(toMap(data_sg,line,params_iso,clnt))

In [321]:
#this is the overall map. Was done previously using slightly different code.
map_sg

In [152]:
map_sg[0][0]

In [153]:
map_sg[1][0]

In [141]:
map_sg[2][0]

In [142]:
map_sg[3][0]

In [143]:
map_sg[4][0]

In [144]:
map_sg[5][0]

In [145]:
map_sg[6][0]

In [146]:
map_sg[][0]

In [147]:
map_sg[8][0]

In [154]:
map_sg[9][0]

In [166]:
map_sg[10][0]

In [212]:
data_sg = dictToDataFrame(map_sg,data_sg)
data_sg

Name STN_NO           X           Y  \
OBJECTID                                                               
100             BENCOOLEN MRT STATION   DT21  29899.2575  31247.3368   
102             PROMENADE MRT STATION   DT15  31064.3414  30586.9146   
103                 BUGIS MRT STATION   DT14  30620.8769  31323.2495   
105            MACPHERSON MRT STATION   DT26  34235.7966  34256.4317   
114           JALAN BESAR MRT STATION   DT22  30466.0301  31970.4313   
...                               ...    ...         ...         ...   
89               RANGGUNG LRT STATION    SE5  35108.5942  40687.1255   
92               SENGKANG LRT STATION    STC  34913.5879  41502.6997   
175       WOODLANDS SOUTH MRT STATION    TE3  23607.8309  45444.7113   
181             WOODLANDS MRT STATION    TE2  22949.0322  46418.5578   
192       WOODLANDS MRT NORTH STATION    TE1         NaN         NaN   

          Latitude   Longitude  COLOR Colour Code               Route Name  \
OBJECTID                                                                     
100       1.298864  103.850380   BLUE     #0354a6            Downtown Line   
102       1.292892  103.860846   BLUE     #0354a6            Downtown Line   
103       1.299551  103.856862   BLUE     #0354a6            Downtown Line   
105       1.326077  103.889336   BLUE     #0354a6            Downtown Line   
114       1.305404  103.855471   BLUE     #0354a6            Downtown Line   
...            ...         ...    ...         ...                      ...   
89        1.384234  103.897176   GREY     #748477             Sengkang LRT   
92        1.391609  103.895424   GREY     #748477             Sengkang LRT   
175       1.427260  103.793863  BROWN     #734538  Thomson-East Coast Line   
181       1.436067  103.787945  BROWN     #734538  Thomson-East Coast Line   
192       1.448379  103.785647  BROWN     #734538  Thomson-East Coast Line   

         Unnamed: 10                                                iso  
OBJECTID                                                                 
100              DTL  {'type': 'FeatureCollection', 'features': [{'t...  
102              DTL  {'type': 'FeatureCollection', 'features': [{'t...  
103              DTL  {'type': 'FeatureCollection', 'features': [{'t...  
105              DTL  {'type': 'FeatureCollection', 'features': [{'t...  
114              DTL  {'type': 'FeatureCollection', 'features': [{'t...  
...              ...                                                ...  
89                SL  {'type': 'FeatureCollection', 'features': [{'t...  
92                SL  {'type': 'FeatureCollection', 'features': [{'t...  
175              TEL  {'type': 'FeatureCollection', 'features': [{'t...  
181              TEL  {'type': 'FeatureCollection', 'features': [{'t...  
192              TEL  {'type': 'FeatureCollection', 'features': [{'t...  

[188 rows x 11 columns]

In [299]:
#saving all the new sg data into a new csv with the isochrone data
data_sg= areaToDataframe(data_sg)
data_sg.to_csv('../resources/data/mrtsg_iso.csv')

# Montreal
Again same methodology but for Montreal

In [256]:
file_name_montreal = '../resources/data/montreal_metro.csv'

data_montreal = pd.read_csv(file_name_montreal, index_col="Stop ID")
print(data_montreal.head())
print(data_montreal.columns)

         Object ID         Name                               Odonym  \
Stop ID                                                                
G1               1    Angrignon  Boulevard Angrignon; Parc Angrignon   
G2               2         Monk                       Boulevard Monk   
G3               3    Jolicoeur                        Rue Jolicoeur   
G4               4       Verdun     Rue de Verdun; borough of Verdun   
G5               5  De L'Église                   Avenue de l'Église   

                                                  Namesake      Opened  \
Stop ID                                                                  
G1                Jean-Baptiste Angrignon, city councillor  03-09-1978   
G2                     James Monk, Quebec Attorney-General  03-09-1978   
G3                     Jean-Moïse Jolicoeur, parish priest  03-09-1978   
G4       Notre-Dame-de-Saverdun, France, hometown of Se...  03-09-1978   
G5                                       Église Sai

In [239]:
map_montreal = folium.Map(tiles='OpenStreetMap', location=(45.5017 , -73.5673), zoom_start=11)
stations_dict_montreal = dictSetup(data_montreal)
for name, station in stations_dict_montreal.items():
    folium.map.Marker(list(reversed(station['locations'])), # reverse coords due to weird folium lat/lon syntax
                        icon=folium.Icon(color='lightgray',
                                            icon_color='#cc0000',
                                            icon='home',
                                            prefix='fa',
                                        ),
                        popup=station['Name'],
                    ).add_to(map_montreal)
map_montreal

In [258]:
lines_montreal = list(data_montreal['Route Name'].unique())
maps_montreal = []
params_iso = {'profile': 'foot-walking', 
              'range': [900], # 900/60 = 15 mins
              'interval': 300,
              'attributes': ['area', 'reachfactor', 'total_pop'] # Get population count for isochrones
             }
for line in lines_montreal:
    maps_montreal.append(toMap(data_montreal,line,params_iso,clnt))

Retrieving Isochrone of G1 station
Success
Retrieving Isochrone of G2 station
Success
Retrieving Isochrone of G3 station
Success
Retrieving Isochrone of G4 station
Success
Retrieving Isochrone of G5 station
Success
Retrieving Isochrone of G6 station
Success
Retrieving Isochrone of G7 station
Success
Retrieving Isochrone of G8 station
Success
Retrieving Isochrone of G9 station
Success
Retrieving Isochrone of G10 station
Success
Retrieving Isochrone of G11 station
Success
Retrieving Isochrone of G12 station
Success
Retrieving Isochrone of G13 station
Success
Retrieving Isochrone of G14 station
Success
Retrieving Isochrone of G15 station
Success
Retrieving Isochrone of G18 station
Success
Retrieving Isochrone of G16 station
Success
Retrieving Isochrone of G17 station
Success
Retrieving Isochrone of G19 station
Success
Retrieving Isochrone of G20 station
Success
Retrieving Isochrone of G21 station
Success
Retrieving Isochrone of G22 station
Success
Retrieving Isochrone of G23 station
Succe

In [259]:
maps_montreal[0][0]

In [260]:
maps_montreal[1][0]

In [261]:
maps_montreal[2][0]

In [262]:
maps_montreal[3][0]

In [ ]:
data_montreal = dictToDataFrame(maps_montreal,data_montreal)
data_montreal.to_csv('montreal_metro_iso.csv')

In [301]:
data_montreal = pd.read_csv('../resources/data/montreal_metro_iso.csv')
data_montreal = areaToDataframe(data_montreal)
data_montreal.to_csv('../resources/data/montreal_metro_iso.csv')

# We've got isochrones!

We're done gathering data. Now to get some stats we'll be doing it in a different notebook as it's getting too long here